In [ ]:
%%capture
!pip install pytorch_lightning
!pip install torch_geometric
!pip install wandb

In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch_geometric.nn as gnn
from torch_geometric import datasets, loader, transforms as T
from torch_geometric.utils import get_laplacian, to_scipy_sparse_matrix
from torch_geometric.data import Data
import pytorch_lightning as pl
from typing import Literal
import multiprocessing
import numpy as np
import wandb

In [ ]:
wandb.login(key=API_KEY)

wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.
wandb: Currently logged in as: hjel2. Use `wandb login --relogin` to force relogin
wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


True

In [ ]:
class AddAdjointEdgeEigenvectorPE(T.BaseTransform):
    def __init__(
            self,
            k,
            is_undirected:bool = False
    ):
        self.enc = T.AddLaplacianEigenvectorPE(k=k, attr_name='adjoint_edge_pe', is_undirected=False)

    def forward(self, data):
        assert data.edge_index is not None
        num_nodes = data.num_nodes
        assert num_nodes is not None

        adj_edge_index = torch.argwhere(data.edge_index[0] == data.edge_index[1].reshape(-1, 1)).transpose(0, 1)
        adjoint = Data(
            edge_index=adj_edge_index,
            num_nodes=data.edge_index.size(1)
        )
        data.adj = self.enc(adjoint).adjoint_edge_pe
        return data

In [ ]:
class AddHyperEdgeEigenvectorPE(T.BaseTransform):
    # Number of nodes from which to use sparse eigenvector computation:
    SPARSE_THRESHOLD: int = 100

    def __init__(
        self,
        k: int
    ):
        self.k = k
        self.is_undirected = True

    def forward(self, data: Data) -> Data:
        assert data.edge_index is not None

        ### start hypergraph specific ###
        num_edges = data.edge_index.size(1) // 2
        assert num_edges is not None

        edge_index = data.edge_index
        mask = edge_index[0] < edge_index[1]
        edge_index = edge_index[:, mask]

        adjacency = (edge_index[0] == edge_index[1].reshape(-1, 1)).int()
        hyper_edge_index = torch.argwhere(adjacency).transpose(0, 1)
        diag = adjacency.sum(-1)
        ### end hypergraph specific ###

        edge_index, edge_weight = get_laplacian(
            hyper_edge_index,
            normalization='sym',
            num_nodes=num_edges,
        )

        ### start hypergraph specific ###
        edge_weight[edge_index[0] == edge_index[1]] = diag[edge_index[0, edge_index[0] == edge_index[1]]].float()
        ### end hypergraph specific ###

        L = to_scipy_sparse_matrix(edge_index, edge_weight, num_edges)

        if num_edges < self.SPARSE_THRESHOLD:
            from numpy.linalg import eig, eigh
            eig_fn = eigh

            eig_vals, eig_vecs = eig_fn(L.todense())  # type: ignore
        else:
            from scipy.sparse.linalg import eigs, eigsh
            eig_fn = eigsh

            eig_vals, eig_vecs = eig_fn(  # type: ignore
                L,
                k=self.k + 1,
                which='SA',
                return_eigenvectors=True,
                **self.kwargs,
            )

        eig_vecs = np.real(eig_vecs[:, eig_vals.argsort()])
        pe = torch.from_numpy(eig_vecs[:, 1:self.k + 1])
        sign = -1 + 2 * torch.randint(0, 2, (self.k, ))
        pe *= sign

        ### start hypergraph specific ###
        encodings_lut = torch.zeros((num_edges, num_edges, self.k))
        encodings_lut[edge_index[0], edge_index[1]] = pe

        pos_encoding = torch.zeros((data.edge_index.size(1), self.k))
        pos_encoding = encodings_lut[edge_index.flatten(), edge_index.flatten().flip(1)]

        data.adj = pos_encoding
        return data
        ### end hypergraph specific ###

In [ ]:
class ZINCDataModule(pl.LightningDataModule):
    def __init__(self, pos_enc, k: int=None, hypr=False):
        super().__init__()
        self.pe = pos_enc
        self.k = k
        self.train_dataset = datasets.ZINC(
            root="~/zincdata",
            split='train',
            subset=True,
            pre_transform=T.Compose([
                T.AddLaplacianEigenvectorPE(k=self.k, attr_name='pe'),
                AddHyperEdgeEigenvectorPE(k=self.k) if hypr else AddAdjointEdgeEigenvectorPE(k=self.k),
                ]) if self.pe else None)
        self.val_dataset = datasets.ZINC(
            root="~/zincdata",
            split='val',
            subset=True,
            pre_transform=T.Compose([
                T.AddLaplacianEigenvectorPE(k=self.k, attr_name='pe'),
                AddHyperEdgeEigenvectorPE(k=self.k) if hypr else AddAdjointEdgeEigenvectorPE(k=self.k),
                ]) if self.pe else None)
        self.test_dataset = datasets.ZINC(
            root="~/zincdata",
            split='test',
            subset=True,
            pre_transform=T.Compose([
                T.AddLaplacianEigenvectorPE(k=self.k, attr_name='pe'),
                AddHyperEdgeEigenvectorPE(k=self.k) if hypr else AddAdjointEdgeEigenvectorPE(k=self.k),
                ]) if self.pe else None)

    def setup(self, stage):
        batch_size = 128
        num_workers = multiprocessing.cpu_count()
        match stage:
            case 'fit':
                self.train_loader = loader.DataLoader(
                    dataset=self.train_dataset,
                    batch_size=batch_size,
                    shuffle=True,
                    num_workers=num_workers,
                )
                self.val_loader = loader.DataLoader(
                    dataset=self.val_dataset,
                    batch_size=batch_size,
                    num_workers=num_workers,
                )
            case 'test':
                self.test_loader = loader.DataLoader(
                    dataset=self.test_dataset,
                    batch_size=batch_size,
                    num_workers=num_workers,
                )

    def train_dataloader(self):
        return self.train_loader

    def val_dataloader(self):
        return self.val_loader

    def test_dataloader(self):
        return self.test_loader

In [ ]:
class GAT(nn.Module):

    def __init__(self, net_params):
        super().__init__()

        in_dim_node = net_params['in_dim']  # node_dim (feat is an integer)
        hidden_dim = net_params['hidden_dim']
        out_dim = net_params['out_dim']
        n_classes = net_params['n_classes']
        num_heads = net_params['n_heads']
        in_feat_dropout = net_params['in_feat_dropout']
        dropout = net_params['dropout']
        n_layers = net_params['L']

        self.readout = net_params['readout']
        self.batch_norm = net_params['batch_norm']
        self.residual = net_params['residual']
        self.dropout = dropout
        self.n_classes = n_classes
        self.device = net_params['device']
        self.pos_enc = net_params['pos_enc']
        edge_in_dim = net_params['edge_in_dim']
        pos_enc_dim = net_params['pos_enc_dim']
        self.edge_enc = net_params['edge_enc']
        self.edge_enc_dim = net_params['edge_enc_dim']

        in_dim = net_params['in_dim']
        if self.pos_enc:
            pos_enc_dim = net_params['pos_enc_dim']
            self.embedding = nn.Embedding(in_dim, hidden_dim*num_heads - pos_enc_dim)
        else:
            self.embedding = nn.Embedding(in_dim, hidden_dim*num_heads)

        edge_feat_dim = net_params['edge_feat_dim']
        edge_enc_dim = net_params['edge_enc_dim']
        if self.edge_enc:
            self.edge_embedding = nn.Embedding(edge_in_dim, edge_feat_dim)
        else:
            self.edge_embedding = nn.Embedding(edge_in_dim, edge_feat_dim + edge_enc_dim)

        self.in_feat_dropout = nn.Dropout(in_feat_dropout)

        self.layers = nn.ModuleList([
            GATLayer(hidden_dim * num_heads,
                     hidden_dim,
                     num_heads,
                     dropout,
                     self.batch_norm,
                     self.residual,
                     edge_dim=edge_feat_dim + edge_enc_dim) for i in range(n_layers - 1)
        ])
        self.layers.append(
            GATLayer(hidden_dim * num_heads,
                     out_dim,
                     1,
                     dropout,
                     self.batch_norm,
                     self.residual,
                     edge_dim=edge_feat_dim + edge_enc_dim))

        self.mlp = nn.Sequential(nn.Linear(out_dim, out_dim // 2, bias=True),
                                 nn.ReLU(inplace=True),
                                 nn.Linear(out_dim // 2, n_classes, bias=True))

    def forward(self,
                x,
                edge_index,
                edge_attr,
                pe=None,
                edge_pe=None,
                agg: Literal[None, 'mean'] = None,
                batch=None):

        # input embedding
        x = self.embedding(x)
        x = self.in_feat_dropout(x)
        if self.pos_enc:
            x = torch.cat((x, pe), -1)

        e = self.edge_embedding(edge_attr - 1)
        if self.edge_enc:
            e = torch.cat((e, edge_pe), -1)

        # GAT
        for i, conv in enumerate(self.layers):
            x = conv(x=x, edge_index=edge_index, edge_attr=e)

        if agg == 'mean':
            aggr = gnn.aggr.MeanAggregation()
            x = aggr(x, batch)

        # output
        h_out = self.mlp(x)

        return h_out


class GATLayer(nn.Module):
    """
    Parameters
    ----------
    in_dim :
        Number of input features.
    out_dim :
        Number of output features.
    num_heads : int
        Number of heads in Multi-Head Attention.
    dropout :
        Required for dropout of attn and feat in GATConv
    batch_norm :
        boolean flag for batch_norm layer.
    residual :
        If True, use residual connection inside this layer. Default: ``False``.
    activation : callable activation function/layer or None, optional.
        If not None, applies an activation function to the updated node features.
    """

    def __init__(self,
                 in_dim,
                 out_dim,
                 num_heads,
                 dropout,
                 batch_norm,
                 residual=False,
                 activation=F.elu,
                 edge_dim=None):
        super().__init__()
        self.residual = residual
        self.activation = activation
        self.batch_norm = batch_norm
        if in_dim != (out_dim * num_heads):
            self.residual = False
        self.gatconv = gnn.GATv2Conv(in_channels=in_dim,
                                     out_channels=out_dim,
                                     heads=num_heads,
                                     dropout=dropout,
                                     edge_dim=edge_dim)
        if self.batch_norm:
            self.batchnorm_h = nn.BatchNorm1d(out_dim * num_heads)

    def forward(self, x, edge_index, edge_attr=None):
        x_in = x  # for residual connection
        x = self.gatconv(x, edge_index, edge_attr=edge_attr).flatten(1)
        if self.batch_norm:
            x = self.batchnorm_h(x)
        if self.activation:
            x = self.activation(x)
        if self.residual:
            x = x_in + x  # residual connection
        return x

In [ ]:
class Model(pl.LightningModule):
    def __init__(self, net_params):
        super().__init__()
        self.net_params = net_params

    def configure_model(self):
        self.model = GAT(self.net_params)

    def configure_optimizers(self):
        return torch.optim.AdamW(
            self.parameters(),
            lr=0.001,
            weight_decay=0.0,
        )

    def forward(self, batch):
        if self.net_params['pos_enc']:
            k = self.net_params['pos_enc_dim']
            sign = torch.tensor([-1, 1])[torch.randint(0, 2, (1, k))].to(self.net_params['device'])
            batch.pe *= sign

        if self.net_params['edge_enc']:
            k = self.net_params['pos_enc_dim']
            sign = torch.tensor([-1, 1])[torch.randint(
                0, 2, (1, self.net_params['pos_enc_dim']))].to(self.net_params['device'])
            batch.adj *= sign

        return self.model(
            x=batch.x.flatten(),
            edge_index=batch.edge_index,
            edge_attr=batch.edge_attr,
            pe=batch.pe,
            edge_pe=batch.adj,
            batch=batch.batch,
            agg="mean",
        )

    def loss(self, batch):
        pred = self(batch)
        label = batch.y

        loss = F.l1_loss(pred.flatten(), label)

        return loss

    def step(self, batch, msg):
        loss = self.loss(batch)
        self.log(f'{msg} loss', loss, batch_size=128, on_epoch=True)
        return loss

    def training_step(self, batch, batch_idx):
        return self.step(batch, 'train')

    def validation_step(self, batch, batch_idx, msg='val'):
        return self.step(batch, 'val')

    def test_step(self, batch, batch_idx):
        return self.step(batch, 'test')

In [ ]:
# from https://github.com/graphdeeplearning/benchmarking-gnns/blob/master/configs/SBMs_node_clustering_GAT_CLUSTER_100k.json
net_params = {
    "L": 4,
    "n_heads": 8,
    "hidden_dim": 18,
    "out_dim": 144,
    "residual": True,
    "readout": "mean",
    "in_feat_dropout": 0.0,
    "dropout": 0.0,
    "batch_norm": True,
    "self_loop": False,
    "pos_enc": True,
    "pos_enc_dim": 8,
    "edge_enc": False,
    "hypergraph_edge_enc": False,
    "edge_enc_dim": 8,
    "edge_feat_dim": 16,
    "device": "cuda",
    "in_dim": 21,
    'edge_in_dim': 3,
    "n_classes": 1,
    "log": True
}

In [ ]:
datamodule = ZINCDataModule(pos_enc=net_params["pos_enc"], k=net_params["edge_enc_dim"], hypr=net_params["hypergraph_edge_enc"])

Extracting /root/zincdata/molecules.zip
Processing...
Processing test dataset: 100%|██████████| 1000/1000 [00:03<00:00, 331.67it/s]
Done!


In [ ]:
for pos_enc, edge_enc, hypr_enc in (
    (False, False, False),
    (False, True, False),
    (False, True, True),
    (True, False, False),
    (True, True, False),
    (True, True, True),
):
    net_params['pos_enc'] = pos_enc
    net_params['edge_enc'] = edge_enc
    net_params['hypergraph_edge_enc'] = hypr_enc

    model = Model(net_params)
    name = 'GAT'
    if net_params['pos_enc']:
        name += '-node'
    if net_params['edge_enc']:
        if net_params['hypergraph_edge_enc']:
            name += '-hyper'
        else:
            name += '-adjoint'
    if net_params['log']:
        logger = pl.loggers.WandbLogger(name=name,
                                        project='Edge-Encodings-ZINC')
        logger.log_hyperparams(net_params)
    trainer = pl.Trainer(
        accelerator='gpu',
        logger=logger if net_params['log'] else False,
        log_every_n_steps=20,
        max_time='00:01:00:00',
        max_epochs=500,
    )
    trainer.fit(model, datamodule)
    trainer.test(model, datamodule, ckpt_path='best')
    if net_params['log']:
        wandb.finish()

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.utilities.rank_zero:You are using a CUDA device ('NVIDIA L4') that has Tensor Cores. To properly utilize them, you should set `torch.set_float32_matmul_precision('medium' | 'high')` which will trade-off precision for performance. For more details, read https://pytorch.org/docs/stable/generated/torch.set_float32_matmul_precision.html#torch.set_float32_matmul_precision
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name  | Type | Params | Mode 
---------------------------------------
0 | model | GAT  | 196 K  | train
---------------------------------------
196 K     Trainable params
0         Non-trainable params
196 K     Total params
0.

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=500` reached.
INFO:pytorch_lightning.utilities.rank_zero:Restoring states from the checkpoint path at ./Edge-Encodings-ZINC/ogdf2kw4/checkpoints/epoch=499-step=39500.ckpt
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.utilities.rank_zero:Loaded model weights from the checkpoint at ./Edge-Encodings-ZINC/ogdf2kw4/checkpoints/epoch=499-step=39500.ckpt


Testing: |          | 0/? [00:00<?, ?it/s]

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│         test loss         │    0.40469083189964294    │
└───────────────────────────┴───────────────────────────┘